## Analyze all my Crypto Data for 5 Years

In [2]:
# Provides ways to work with large multidimensional arrays
import numpy as np 
# Allows for further data manipulation and analysis
import pandas as pd 
import matplotlib.pyplot as plt # Plotting
import matplotlib.dates as mdates # Styling dates
%matplotlib inline
# conda install -c conda-forge matplotlib
import datetime as dt # For defining dates
import time

# conda install -c conda-forge multitasking
# pip install -i https://pypi.anaconda.org/ranaroussi/simple yfinance

import yfinance as yf
import os

# conda install -c conda-forge cufflinks-py
# conda install -c plotly plotly
import cufflinks as cf
import plotly.express as px
import plotly.graph_objects as go

# Make Plotly work in your Jupyter Notebook
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
# Use Plotly locally
cf.go_offline()

from plotly.subplots import make_subplots

# New Imports
# Used to get data from a directory
import os
from os import listdir
from os.path import isfile, join

import warnings
warnings.simplefilter("ignore")

## Constants

In [3]:
PATH = ""

# Start end date defaults
S_DATE = "2016-12-12"
E_DATE = dt.datetime.today().strftime('%Y-%m-%d')
print('from:',S_DATE,'to:', E_DATE)
S_DATE_DT = pd.to_datetime(S_DATE)
E_DATE_DT = pd.to_datetime(E_DATE)

from: 2016-12-12 to: 2022-01-22


## Holds Stocks Not Downloaded

In [4]:
stocks_not_downloaded = []
missing_stocks = []

## Get Tickers

In [101]:

tickers = ['ETH-USD', 'BTC-USD', 'BCH-USD', 'ZRX-USD','XRP-USD'  ]

for x in tickers:
    print(x, end=", ")
print(len(tickers))

ETH = yf.download(tickers[0], start=S_DATE, end=E_DATE, interval='1d')
BTC = yf.download(tickers[1], start=S_DATE, end=E_DATE, interval='1d')
BCH = yf.download(tickers[2], start=S_DATE, end=E_DATE, interval='1d')
ZRX = yf.download(tickers[3], start=S_DATE, end=E_DATE, interval='1d')
XRP = yf.download(tickers[4], start=S_DATE, end=E_DATE, interval='1d')
len(ETH),len(BTC),len(BCH),len(ZRX),len(XRP)

ticker_dict = {'ETH': ETH, 'BTC': BTC, 'BCH': BCH, 'ZRX': ZRX, 'XRP': XRP}


ETH-USD, BTC-USD, BCH-USD, ZRX-USD, XRP-USD, 5
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


## Are my Crypto Worth Investing in?

In [6]:
fig = go.Figure()

eth_plot = go.Scatter(x=ETH.index, y=ETH['Close'], name="ETH")
btc_plot = go.Scatter(x=BTC.index, y=BTC['Close'], name="BTC")
bch_plot = go.Scatter(x=BCH.index, y=BCH['Close'], name="BCH")
zrx_plot = go.Scatter(x=ZRX.index, y=ZRX['Close'], name="ZRX")
xrp_plot = go.Scatter(x=XRP.index, y=XRP['Close'], name="XRP")   

# Plot price changes
fig.add_trace(eth_plot)
fig.add_trace(btc_plot)
fig.add_trace(bch_plot)
fig.add_trace(zrx_plot)
fig.add_trace(xrp_plot)
    
fig.update_xaxes(title="Date", rangeslider_visible=True)
fig.update_yaxes(title="Price")
fig.update_layout(height=800, width=900,  showlegend=True)
fig.show()

# This data isn't useful for our purposes because the scales are different
# We must calculate the daily returns for these stocks to get data we can
# work with



## Daily Returns

For single stocks to find the daily return we subtract opening price from the closing price. Then you could multiply by the number of shares owned.

We calculate a percentage rate of return for each day to compare investments.
Simple Rate of Return = (End Price - Beginning Price) / Beginning Price OR (EP / BP) - 1

In [7]:
# Shift provides the value from the previous day
# NaN is displayed because there was no previous day price for the 1st calculation
def add_daily_return_to_df(df):
    df['daily_return'] = (df['Close'] / df['Close'].shift(1)) - 1
    
    return df  

## Get Cumulative Return

In [9]:
def add_cum_return_to_df(df):
    df['cum_return'] = (1 + df['daily_return']).cumprod()
    return df

In [23]:
for ticker in ticker_dict:
    add_daily_return_to_df(ticker_dict[ticker])
    add_cum_return_to_df(ticker_dict[ticker])

ZRX.head()


Open      High       Low     Close  Adj Close    Volume  \
Date                                                                      
2017-08-16  0.111725  0.280031  0.103962  0.224399   0.224399   5232600   
2017-08-17  0.223022  0.238935  0.206735  0.206735   0.206735   2752410   
2017-08-18  0.205558  0.350260  0.205558  0.293387   0.293387  12793800   
2017-08-19  0.294578  0.543728  0.284357  0.478768   0.478768  52677500   
2017-08-20  0.471296  0.475262  0.403409  0.424265   0.424265  16016500   

            daily_return  cum_return  
Date                                  
2017-08-16           NaN         NaN  
2017-08-17     -0.078717    0.921283  
2017-08-18      0.419145    1.307435  
2017-08-19      0.631865    2.133557  
2017-08-20     -0.113840    1.890672

## Merge Multiple Stocks in One Dataframe by Column Name

In [31]:
def merge_df_by_column_name(col_name, sdate, edate, ticker_dict):
    # Will hold data for all dataframes with the same column name
    mult_df = pd.DataFrame()
    # Loop through all tickers
    for k,d in ticker_dict.items():
        # print(k)
        mask = (d.index >= sdate) & (d.index <= edate)
        mult_df[k] = d.loc[mask][col_name]
        
    return mult_df


In [33]:
mult_df = merge_df_by_column_name('cum_return',  S_DATE, 
                                  E_DATE, ticker_dict)
mult_df.sample(5)

ETH        BTC       BCH       ZRX       XRP
Date                                                         
2018-04-04  1.185921   8.904201  0.992195  2.324159  2.306477
2021-06-08  7.845323  43.486143  0.912562  4.265901  4.026833
2017-12-08  1.421171  21.526222  2.237694  1.192496  1.159259
2021-04-15  7.850551  82.254723  1.326840  9.829701  8.120296
2021-02-12  5.745168  61.716172  0.882778  8.044946  2.798278

In [34]:
# Plot out cumulative returns on $1 in each stock since beginning of 2017
fig = px.line(mult_df, x=mult_df.index, y=mult_df.columns)
fig.update_xaxes(title="Date", rangeslider_visible=True)
fig.update_yaxes(title="Price")
fig.update_layout(height=800, width=900, 
                  showlegend=True)
fig.show()

## Create a Price / Volume Chart

In [56]:
fig = go.Figure()
eth_plot = go.Scatter(x=ETH.index, y=ETH['Close'], name="ETH")

# Plot price changes
fig.add_trace(eth_plot)

# Plot volume as bar graph
fig.add_trace(go.Bar(x=ETH.index, y=ETH['Volume']/20000000, name='Volume Traded',  marker_color='red'))

fig.update_xaxes(title="Date", rangeslider_visible=True)
fig.update_yaxes(title="Price")
fig.update_layout(height=800, width=1200, 
                  showlegend=True)
fig.show()


## Adding Bollinger Bands

Bollinger Bands plot 2 lines using a moving average and the standard deviation defines how far apart the lines are. They also are used to define if prices are to high or low. When bands tighten it is believed a sharp price move in some direction. Prices tend to bounce off of the bands which provides potential market actions.

A strong trend should be noted if the price moves outside the band. If prices go over the resistance line it is in overbought territory and if it breaks through support it is a sign of an oversold position.

You normally use 20 sessions when using them.

In [57]:
# Here we will add a middle band (20 days), upper band (20 days + 1.96 std),
# and lower band (20 days - 1.96 std)
def add_bollinger_bands(df):
    df['middle_band'] = df['Close'].rolling(window=20).mean()
    df['upper_band'] = df['middle_band'] + 1.96 * df['Close'].rolling(window=20).std()
    df['lower_band'] = df['middle_band'] - 1.96 * df['Close'].rolling(window=20).std()

In [62]:
for _,d in ticker_dict.items():
    add_bollinger_bands(d)

In [64]:
XRP.tail()

Open      High       Low     Close  Adj Close      Volume  \
Date                                                                        
2022-01-17  0.778999  0.780180  0.752352  0.762742   0.762742  1406443014   
2022-01-18  0.762769  0.768049  0.739464  0.752631   0.752631  1510069237   
2022-01-19  0.752614  0.753155  0.726485  0.739749   0.739749  1446126322   
2022-01-20  0.739726  0.761583  0.719402  0.719421   0.719421  1251475248   
2022-01-21  0.719609  0.728245  0.623196  0.635738   0.635738  3150758603   

            daily_return  cum_return  middle_band  upper_band  lower_band  
Date                                                                       
2022-01-17     -0.020813    3.507053     0.792491    0.863432    0.721551  
2022-01-18     -0.013256    3.460563     0.789287    0.861354    0.717220  
2022-01-19     -0.017116    3.401332     0.784292    0.855539    0.713045  
2022-01-20     -0.027480    3.307865     0.778705    0.851894    0.705516  
2022-01-21     -0.116320    2.923095     0.768018    0.857544    0.678493

## Plot with Bollinger Bands

In [68]:
def plot_with_boll_bands(ticker_dict,ticker):
    df = ticker_dict[ticker]
    add_bollinger_bands(df)
    
    fig = go.Figure()

    candle = go.Candlestick(x=df.index, open=df['Open'],
    high=df['High'], low=df['Low'],
    close=df['Close'], name="Candlestick")

    upper_line = go.Scatter(x=df.index, y=df['upper_band'], 
    line=dict(color='rgba(250, 0, 0, 0.75)', 
    width=1), name="Upper Band")

    mid_line = go.Scatter(x=df.index, y=df['middle_band'], 
    line=dict(color='rgba(0, 0, 250, 0.75)', 
    width=0.7), name="Middle Band")

    lower_line = go.Scatter(x=df.index, y=df['lower_band'], 
    line=dict(color='rgba(0, 250, 0, 0.75)', 
    width=1), name="Lower Band")

    fig.add_trace(candle)
    fig.add_trace(upper_line)
    fig.add_trace(mid_line)
    fig.add_trace(lower_line)

    fig.update_xaxes(title="Date", rangeslider_visible=True)
    fig.update_yaxes(title="Price")
    fig.update_layout(title=ticker + " Bollinger Bands", 
    height=800, width=1200, showlegend=True)
    fig.show()

In [69]:
plot_with_boll_bands(ticker_dict,'ETH')

## Support & Resistance

We normally use multiple moving averages to develop our support and resistance lines. 50 day for medium, 100 for long and 200 for very long terms are commonly used.

## Calculate Moving Averages

Moving averages are used to mitigate short term flucuations in a stock price. We create them by calculating the mean of a set of prices over a specified number of time periods. The Simple moving average (SMA) is just a simple mean. An Exponential Moving Average (EMA) is a weighted average that put more emphasis on more recent data.

In [ ]:
def get_SMA(df_, col_name):
    df=df_.copy()
    df['MA50'] = df[col_name].rolling(50).mean()
    df['MA100'] = df[col_name].rolling(100).mean()
 
    # EMA If we set adjust to False the weighted function is calculated recursively
    df['EMA20'] = df[col_name].ewm(span=20, adjust=False).mean()
    df['EMA50'] = df[col_name].ewm(span=50, adjust=False).mean()
    df['EMA100'] = df[col_name].ewm(span=100, adjust=False).mean()
    return df

# get_SMA(ETH,'Close')

## Plotting Moving Averages

In [73]:
def plot_moving_averages(df_, col_name):
    df=df_.copy()
    df = get_SMA(df, col_name)
    
    fig = go.Figure()

    candle = go.Candlestick(x=df.index, open=df['Open'],
        high=df['High'], low=df['Low'],
        close=df['Close'], name="Candlestick")

    ema50_line = go.Scatter(x=df.index, y=df['EMA50'], 
        line=dict(color='rgba(250, 0, 0, 0.75)', 
        width=1), name="EMA50")

    ema100_line = go.Scatter(x=df.index, y=df['EMA100'], 
        line=dict(color='rgba(0, 250, 0, 0.75)', 
        width=1), name="EMA100")

    fig.add_trace(candle)
    # 1st support line
    fig.add_trace(ema50_line)
    # 2nd support line
    fig.add_trace(ema100_line)
    fig.show()
    
plot_moving_averages(ETH,'Close')
# What we see with the support line is that if we hit it the market bounces back. When candles are green that means we have more buyers than sellers and vice versa.
# Support levels are good indicators and the market normally only breaks support when an event occurs that is external to the market.

## Short Term Plot Function

In [93]:
def plot_short_term(ticker):
    df = yf.download(tickers=ticker, period='3d', interval='15m')
    df['MA5'] = df['Close'].rolling(5).mean()
    df['MA20'] = df['Close'].rolling(20).mean()
    fig = go.Figure()
    
    candle = go.Candlestick(x=df.index, open=df['Open'],
        high=df['High'], low=df['Low'],
        close=df['Close'], name="Candlestick")

    ma5_line = go.Scatter(x=df.index, y=df['MA5'], 
    line=dict(color='rgba(255,165,0, 0.75)', 
    width=1), name="MA5")

    ma20_line = go.Scatter(x=df.index, y=df['MA20'], 
    line=dict(color='rgba(0, 0, 250, 0.75)', 
    width=1), name="MA20")

    fig.add_trace(candle)
    fig.add_trace(ma5_line)
    fig.add_trace(ma20_line)
    
    fig.update_layout(title=ticker + " Short Term",
                      height=800, width=1200, showlegend=True)

    fig.show()


## Long Term Plot Function

In [94]:
def plot_long_term(ticker):
    df = yf.download(tickers=ticker, period='3mo', interval='1d')
    df['MA5'] = df['Close'].rolling(5).mean()
    df['MA20'] = df['Close'].rolling(20).mean()
    fig = go.Figure()

    candle = go.Candlestick(x=df.index, open=df['Open'],
        high=df['High'], low=df['Low'],
        close=df['Close'], name="Candlestick")

    ma5_line = go.Scatter(x=df.index, y=df['MA5'], 
    line=dict(color='rgba(255,165,0, 0.75)', 
    width=1), name="MA5")

    ma20_line = go.Scatter(x=df.index, y=df['MA20'], 
    line=dict(color='rgba(0, 0, 250, 0.75)', 
    width=1), name="MA20")

    fig.add_trace(candle)
    fig.add_trace(ma5_line)
    fig.add_trace(ma20_line)

    fig.update_layout(title=ticker + " Long Term",  height=800, width=1200, showlegend=True)
    fig.show()

## Long Term Ethereum Plot

In [95]:
plot_long_term('ETH-USD')

[*********************100%***********************]  1 of 1 completed


## Short Term Ethereum Plot

In [96]:
plot_short_term('ETH-USD')

[*********************100%***********************]  1 of 1 completed


## Returns a DF with Cumulative Return for all Stocks

In [97]:
mult_df = merge_df_by_column_name('cum_return',  S_DATE,
                                  E_DATE, ticker_dict)
mult_df.sample(5)


ETH        BTC       BCH       ZRX       XRP
Date                                                         
2017-11-17  1.035870  10.015174  1.811821  0.816064  1.041809
2020-12-03  1.921906  25.262589  0.446728  1.915802  2.903530
2019-09-08  0.565175  13.564838  0.469217  0.720926  1.209648
2017-12-04  1.465340  15.144511  2.410076  0.996257  1.165908
2020-05-22  0.645620  11.929592  0.358402  1.491673  0.921168

## Ichimoku Kinko Hyo

The Ichimoku (One Look) is considered an all in one indicator. It provides information on momentum, support and resistance. It is made up of 5 lines. If you are a short term trader you create 1 minute or 6 hour. Long term traders focus on day or weekly data.

 - Conversion Line (Tenkan-sen) : Represents support, resistance and reversals. Used to measure short term trends.
 - Baseline (Kijun-sen) : Represents support, resistance and confirms trend changes. Allows you to evaluate the strength of medium term trends. Called the baseline because it lags the price.
 - Leading Span A (Senkou A) : Used to identify future areas of support and resistance
 - Leading Span B (Senkou B) : Other line used to identify suture support and resistance
 - Lagging Span (Chikou) : Shows possible support and resistance. It is used to confirm signals obtained from other lines.
 - Cloud (Kumo) : Space between Span A and B. Represents the divergence in price evolution.
 
Formulas

 - Lagging Span = Price shifted back 26 periods
 - Base Line = (Highest Value in period + Lowest value in period)/2 (26 Sessions)
 - Conversion Line = (Highest Value in period + Lowest value in period)/2 (9 Sessions)
 - Leading Span A = (Conversion Value + Base Value)/2 (26 Sessions)
 - Leading Span B = (Conversion Value + Base Value)/2 (52 Sessions)

## Get Ichimoku Function

In [98]:
def get_fill_color(label):
    if label >= 1:
        return 'rgba(0,250,0,0.4)'
    else:
        return 'rgba(250,0,0,0.4)'

In [102]:
def get_Ichimoku_all(ticker_df):
    df = ticker_df.copy()

    # Conversion
    hi_val = df['High'].rolling(window=9).max()
    low_val = df['Low'].rolling(window=9).min()
    df['Conversion'] = (hi_val + low_val) / 2

    # Baseline
    hi_val2 = df['High'].rolling(window=26).max()
    low_val2 = df['Low'].rolling(window=26).min()
    df['Baseline'] = (hi_val2 + low_val2) / 2

    # Spans
    df['SpanA'] = ((df['Conversion'] + df['Baseline']) / 2).shift(26)
    hi_val3 = df['High'].rolling(window=52).max()
    low_val3 = df['Low'].rolling(window=52).min()
    df['SpanB'] = ((hi_val3 + low_val3) / 2).shift(26)
    df['Lagging'] = df['Close'].shift(-26)

    candle = go.Candlestick(x=df.index, open=df['Open'],
    high=df['High'], low=df["Low"], close=df['Close'], name="Candlestick")

    df1 = df.copy()
    fig = go.Figure()
    df['label'] = np.where(df['SpanA'] > df['SpanB'], 1, 0)
    df['group'] = df['label'].ne(df['label'].shift()).cumsum()

    df = df.groupby('group')

    dfs = []
    for name, data in df:
        dfs.append(data)

    for df in dfs:
        fig.add_traces(go.Scatter(x=df.index, y=df.SpanA,
        line=dict(color='rgba(0,0,0,0)')))

        fig.add_traces(go.Scatter(x=df.index, y=df.SpanB,
        line=dict(color='rgba(0,0,0,0)'),
        fill='tonexty',
        fillcolor=get_fill_color(df['label'].iloc[0])))

    baseline = go.Scatter(x=df1.index, y=df1['Baseline'], 
    line=dict(color='pink', width=2), name="Baseline")

    conversion = go.Scatter(x=df1.index, y=df1['Conversion'], 
    line=dict(color='black', width=1), name="Conversion")

    lagging = go.Scatter(x=df1.index, y=df1['Lagging'], 
    line=dict(color='purple', width=2), name="Lagging")

    span_a = go.Scatter(x=df1.index, y=df1['SpanA'], 
    line=dict(color='green', width=2, dash='dot'), name="Span A")

    span_b = go.Scatter(x=df1.index, y=df1['SpanB'], 
    line=dict(color='red', width=1, dash='dot'), name="Span B")

    fig.add_trace(candle)
    fig.add_trace(baseline)
    fig.add_trace(conversion)
    fig.add_trace(lagging)
    fig.add_trace(span_a)
    fig.add_trace(span_b)
    
    fig.update_layout(height=800, width=1200, showlegend=True, title_text=ticker)
    
    fig.show()
    return df

## What the Lines Mean
- Lagging Span : (Dark Purple) When above the price it is bullish and when below bearish. It is used with other indicators because it is mainly a filter.
 - Baseline : (Pink) When below price this is considered support. When above price this is considered resistance. We are in an uptrend when the slope increases and vice versa. The slope of the curve tells us the strength of the trend.
 - Conversion : (Black) We focus on its position versus the Baseline. When the Conversion crosses above the Baseline we are in an upward trend and vice versa. This is considered a strong indicator when above the Cloud and weak when below.
 - Cloud : The thicker the Cloud, the stronger the trend and vice versa. When the Spans cross many times we are in a range. When they cross this is a sign of a reversal of trend. 

- Focus on Past : Lagging Span (Chikou)
- Focus on Present : Baseline (Kijun-sen) & Conversion Line (Tenkan-sen)
- Focus on Future : Cloud (Kumo)

## Is The Ichimoku Accurate?

## Add Ichimoku Data to Dataframe

In [207]:
def add_Ichimoku_to_df(ticker, period, interval):
    df = yf.download(tickers=ticker, period=period, interval=interval)

    # Conversion
    hi_val = df['High'].rolling(window=9).max()
    low_val = df['Low'].rolling(window=9).min()
    df['Conversion'] = (hi_val + low_val) / 2

    # Baseline
    hi_val2 = df['High'].rolling(window=26).max()
    low_val2 = df['Low'].rolling(window=26).min()
    df['Baseline'] = (hi_val2 + low_val2) / 2

    # Span A
    df['SpanA'] = ((df['Conversion'] + df['Baseline']) / 2).shift(26)

    # Span B
    hi_val3 = df['High'].rolling(window=52).max()
    low_val3 = df['Low'].rolling(window=52).min()
    df['SpanB'] = ((hi_val3 + low_val3) / 2).shift(26)

    # Lagging Span
    df['Lagging'] = df['Close'].shift(-26)

    return df

In [209]:
ETH_tst = add_Ichimoku_to_df("ETH-USD", "10y", "1d")
ETH_tst.sample(5)

[*********************100%***********************]  1 of 1 completed


Open         High          Low        Close    Adj Close  \
Date                                                                          
2019-07-09   313.325165   318.223114   305.285828   308.881012   308.881012   
2021-12-08  4311.674316  4453.112305  4234.537598  4439.357910  4439.357910   
2020-04-16   153.200424   173.157272   150.359421   172.157379   172.157379   
2019-05-10   170.312973   175.885269   168.991425   173.142746   173.142746   
2020-07-23   262.388641   277.583466   261.047089   274.689056   274.689056   

                 Volume   Conversion     Baseline        SpanA        SpanB  \
Date                                                                          
2019-07-09  10055159803   295.412842   307.773056   251.969902   219.643654   
2021-12-08  18704315119  4153.113281  4208.599365  4435.182495  3800.471802   
2020-04-16  22910469236   161.784843   148.536007   151.663475   191.153996   
2019-05-10   8036919053   170.047531   166.240044   165.818901   154.890278   
2020-07-23  10281309262   254.602318   248.528069   235.464794   216.470169   

                Lagging  
Date                     
2019-07-09   222.669724  
2021-12-08  3761.380371  
2020-04-16   189.312500  
2019-05-10   247.051010  
2020-07-23   423.669312

## Plot Ichimoku

In [133]:
def plot_ichimoku(df):
    candle = go.Candlestick(x=df.index, open=df['Open'],
    high=df['High'], low=df["Low"], close=df['Close'], name="Candlestick")

    df1 = df.copy()
    fig = go.Figure()
    df['label'] = np.where(df['SpanA'] > df['SpanB'], 1, 0)
    df['group'] = df['label'].ne(df['label'].shift()).cumsum()

    df = df.groupby('group')

    dfs = []
    for name, data in df:
        dfs.append(data)

    for df in dfs:
        fig.add_traces(go.Scatter(x=df.index, y=df.SpanA,
        line=dict(color='rgba(0,0,0,0)')))

        fig.add_traces(go.Scatter(x=df.index, y=df.SpanB,
        line=dict(color='rgba(0,0,0,0)'),
        fill='tonexty',
        fillcolor=get_fill_color(df['label'].iloc[0])))

    baseline = go.Scatter(x=df1.index, y=df1['Baseline'], 
    line=dict(color='pink', width=2), name="Baseline")

    conversion = go.Scatter(x=df1.index, y=df1['Conversion'], 
    line=dict(color='black', width=1), name="Conversion")

    lagging = go.Scatter(x=df1.index, y=df1['Lagging'], 
    line=dict(color='purple', width=2), name="Lagging")

    span_a = go.Scatter(x=df1.index, y=df1['SpanA'], 
    line=dict(color='green', width=2, dash='dot'), name="Span A")

    span_b = go.Scatter(x=df1.index, y=df1['SpanB'], 
    line=dict(color='red', width=1, dash='dot'), name="Span B")

    fig.add_trace(candle)
    fig.add_trace(baseline)
    fig.add_trace(conversion)
    fig.add_trace(lagging)
    fig.add_trace(span_a)
    fig.add_trace(span_b)
    
    fig.update_layout(height=800, width=1200, showlegend=True)

    fig.show()

In [210]:
def get_Ichimoku(df, file):

    candle = go.Candlestick(x=df.index, open=df['Open'],
                            high=df['High'], low=df["Low"], close=df['Close'], name="Candlestick")

    df1 = df.copy()
    fig = go.Figure()
    df['label'] = np.where(df['SpanA'] > df['SpanB'], 1, 0)
    df['group'] = df['label'].ne(df['label'].shift()).cumsum()

    df = df.groupby('group')

    dfs = []
    for name, data in df:
        dfs.append(data)

    for df in dfs:
        fig.add_traces(go.Scatter(x=df.index, y=df.SpanA,line=dict(color='rgba(0,0,0,0)')))

        fig.add_traces(go.Scatter(x=df.index, y=df.SpanB,
                                  line=dict(color='rgba(0,0,0,0)'),
                                  fill='tonexty',
                                  fillcolor=get_fill_color(df['label'].iloc[0])))

    baseline = go.Scatter(x=df1.index, y=df1['Baseline'],line=dict(color='pink', width=2), name="Baseline")

    conversion = go.Scatter(x=df1.index, y=df1['Conversion'],line=dict(color='black', width=1), name="Conversion")

    lagging = go.Scatter(x=df1.index, y=df1['Lagging'],line=dict(color='purple', width=2), name="Lagging")

    span_a = go.Scatter(x=df1.index, y=df1['SpanA'],line=dict(color='green', width=2, dash='dot'), name="Span A")

    span_b = go.Scatter(x=df1.index, y=df1['SpanB'],line=dict(color='red', width=1, dash='dot'), name="Span B")

    fig.add_trace(candle)
    fig.add_trace(baseline)
    fig.add_trace(conversion)
    fig.add_trace(lagging)
    fig.add_trace(span_a)
    fig.add_trace(span_b)

    fig.update_layout(height=1200, width=1200, showlegend=True)

    fig.show()  # save plot as gif

    fig.write_image(str(file)+".png")

In [211]:
ETH_tst = add_Ichimoku_to_df('ETH-USD', '1y', '1d')
get_Ichimoku(ETH_tst, 'ETH')


[*********************100%***********************]  1 of 1 completed


## Add Buy & Sell Data to Dataframe

In [ ]:
# Cloud_Stat column will be 1 when above, -1 when below and 0 otherwise
# A_Over_B_Stat will be 1 when Span A is above Span B and -1 otherwise

# Baseline (Kijun-sen) & Conversion Line (Tenkan-sen)
# Conv_Over_Base_Stat when conversion over baseline 1 and -1 otherwise 
# Price_Over_Conv_Stat when conversion over price -1 and 1 otherwise

# We will use the above indicators to calculate whether to Buy, Sell or Hold
# We buy when above the cloud and sell when below
# When Span A is above Span B buy and vice versa
# When Conversion over Baseline buy and vice versa
# When Price over Conversion buy and vice versa

In [108]:
# print the df name
def get_df_name(df):
    name = [x for x in globals() if globals()[x] is df][0]
    return name


In [110]:
def calc_buy_and_sell(df):
    # Assign 1 or -1 based on if span a & b are above the open price
    df['over_cloud'] = np.where((df['Open'] >= df['SpanA']) & (df['Open'] >= df['SpanB']), 1, -1)
    
    # Assign 1 or -1 based on if span a is over span b
    df['a_over_b'] = np.where((df['SpanA'] >= df['SpanB']), 1, -1)

    # Add 1 or -1 based on if the conversion is over the baseline
    df['conv_over_base'] = np.where((df['Conversion'] >= df['Baseline']), 1, -1)

    # Add 1 or -1 based on if open price is over the conversion
    df['price_over_conv'] = np.where((df['Open'] >= df['Conversion']), 1, -1)

    # Delete rows that contain NaN values
    df.dropna(subset=["SpanA", "SpanB"], inplace=True)   # Lagging?

    # Add up weighting that determines if we buy or sell
    df['position'] = df['over_cloud'] + df['a_over_b'] + df['conv_over_base'] + df['price_over_conv']

    return df

In [205]:
ETH_tst = calc_buy_and_sell(ETH_tst)
ETH_tst.tail()

Open         High          Low        Close    Adj Close  \
Date                                                                          
2022-01-19  3163.850342  3171.158447  3055.212402  3095.825928  3095.825928   
2022-01-20  3095.271729  3265.336914  3000.908203  3001.120117  3001.120117   
2022-01-21  3002.956787  3029.081055  2496.812988  2557.931641  2557.931641   
2022-01-22  2561.145264  2615.247314  2330.247314  2405.181152  2405.181152   
2022-01-23  2405.749756  2540.795898  2397.023193  2440.982422  2440.982422   

                 Volume   Conversion     Baseline        SpanA        SpanB  \
Date                                                                          
2022-01-19  13187424144  3228.216187  3543.124268  4041.669495  4208.599365   
2022-01-20  10645922764  3201.064087  3536.842529  4041.669495  4208.599365   
2022-01-21  26796291874  2946.891357  3311.407227  4053.664185  4208.599365   
2022-01-22  27369692036  2853.324219  3183.892700  4020.303345  4208.599365   
2022-01-23  18113075200  2853.324219  3103.516235  4020.303345  4208.599365   

            ...  label  group  over_cloud  a_over_b  conv_over_base  \
Date        ...                                                       
2022-01-19  ...      0     25          -1        -1              -1   
2022-01-20  ...      0     25          -1        -1              -1   
2022-01-21  ...      0     25          -1        -1              -1   
2022-01-22  ...      0     25          -1        -1              -1   
2022-01-23  ...      0     25          -1        -1              -1   

            price_over_conv  position  daily_return  inv_val     tot_val  
Date                                                                      
2022-01-19               -1        -4     -0.021555       48  448.620000  
2022-01-20               -1        -4     -0.030591       48  434.896063  
2022-01-21                1        -2     -0.147674       48  370.673067  
2022-01-22               -1        -4     -0.059716       48  348.537804  
2022-01-23               -1        -4      0.014885       48  353.725810  

[5 rows x 21 columns]

In [125]:
# Add daily return to DF
ETH_tst = add_daily_return_to_df(ETH_tst)
ETH_tst.head()

Open         High          Low        Close    Adj Close  \
Date                                                                          
2021-04-09  2088.772217  2102.873779  2055.163330  2072.108887  2072.108887   
2021-04-10  2071.111572  2196.996338  2062.787598  2135.942139  2135.942139   
2021-04-11  2136.156982  2165.191406  2119.865723  2157.656982  2157.656982   
2021-04-12  2157.361816  2199.718750  2110.368896  2139.353271  2139.353271   
2021-04-13  2139.364258  2318.423340  2138.559570  2299.187744  2299.187744   

                 Volume   Conversion     Baseline        SpanA        SpanB  \
Date                                                                          
2021-04-09  19812472092  2032.315186  1856.411194  1698.386322  1541.441528   
2021-04-10  24986243611  2071.219238  1878.683411  1727.742157  1618.589905   
2021-04-11  19692836132  2071.219238  1878.683411  1736.336548  1625.798889   
2021-04-12  21727936609  2072.580444  1880.044617  1748.614349  1625.798889   
2021-04-13  29456642939  2131.932739  1939.396912  1729.523346  1625.798889   

                Lagging  label  group  over_cloud  a_over_b  conv_over_base  \
Date                                                                          
2021-04-09  3522.783203      1      2           1         1               1   
2021-04-10  3490.880371      1      2           1         1               1   
2021-04-11  3484.729004      1      2           1         1               1   
2021-04-12  3902.647705      1      2           1         1               1   
2021-04-13  3928.844727      1      2           1         1               1   

            price_over_conv  position  daily_return      inv_val  
Date                                                              
2021-04-09                1         4           NaN  2088.772217  
2021-04-10               -1         2      0.030806  2153.118798  
2021-04-11                1         4      0.010166  2175.008267  
2021-04-12                1         4     -0.008483  2156.557362  
2021-04-13                1         4      0.074712  2317.677180

## Test Ichimoku

In [212]:
def test_ichimoku(ticker, period, interval, plot=True):
    df = add_Ichimoku_to_df(ticker, period, interval)
    if plot:
        plot_ichimoku(df)
    df = calc_buy_and_sell(df)
    df = add_daily_return_to_df(df)

    df['inv_val'] = 0   # how much is invested
    df['tot_val'] = 0   # how much is the total value incl profit/loss
    prev_inv_val = 0
    prev_tot_val = 0
    can_buy = True

    # Cycle through rows and buy when the cloud is greater than 2
    for index, row in df.iterrows():
        
        if pd.isnull(row['daily_return']):
            df.loc[index, 'inv_val'] = prev_inv_val
            df.loc[index, 'tot_val'] = prev_tot_val
            continue
        
        row['inv_val'] = prev_inv_val  # start value for the day is the previous day's value
        row['tot_val'] = prev_tot_val  # start value for the day is the previous day's value
        row['tot_val'] += prev_tot_val * row['daily_return'] # update the total value with the daily return
        
        if row['position'] >= 2:   # Buy signal
            if can_buy:
                row['inv_val'] += 1  #row['Open']
                row['tot_val'] += 1  #row['Open']
                can_buy=False
        else:
            can_buy=True  # can buy again
               
        # Store the investment total in the original dataframe
        df.loc[index, 'inv_val'] = row['inv_val']
        df.loc[index, 'tot_val'] = row['tot_val']
        
        # Save the previous day investment so we can use it in calculations
        prev_inv_val = row['inv_val']
        prev_tot_val = row['tot_val']

    return df


In [213]:
# Ichimoku works better with non-diversified assets
ETH_tst = test_ichimoku('ETH-USD', "10y", "1d", plot=True)
# px.line(ETH_tst, x=ETH_tst.index, y=ETH_tst[['Open', 'inv_val']],
#         labels={'x': 'Date', 'y': 'Value of Dollar'},
#         title='Ichimoku vs "do nothing" for ETC_tst')

[*********************100%***********************]  1 of 1 completed


In [214]:
ETH_plot = ETH_tst[['Close','inv_val','tot_val']]
ETH_plot.Close = ETH_plot.Close/10
ETH_plot.iplot(kind='line',  y=['Close','inv_val','tot_val'],
                title='Ichimoku "investera 1$" vs vinst för ETC_tst')